## Multi-Agent Financial Analysis System
#### A Collaborative Agentic AI for Market Insight Generation
<br>

### Aliaksei Matsarski,Ian Rebmann –  Team 6
### AAI-520-03 – Natural Language Processing and GenAI
### Instructor: Mirsardar Esnaeilli, Ph.D
### Shiley-Marcos School of Engineering, University of San Diego
### October 20, 2025


## 1. Overview

This notebook implements a Multi-Agent Financial Analysis System powered by agentic AI. It orchestrates specialized LLM agents to analyze market news, earnings reports, and stock data, producing structured, explainable investment insights.
Unlike traditional single-pipeline systems, this framework enables reasoning, task routing, self-critique, and iterative refinement — mirroring professional financial research workflows.

## 2. LLM Initialization

Initializes the OpenAI-compatible ChatOpenAI model and environment configuration.
This step defines model parameters (e.g., temperature, model name) and API keys. It ensures reproducibility and sets up the base reasoning component shared by all agents.

In [ ]:
import os
from langchain_openai import ChatOpenAI

def init_main_model(llm_model_name: str):
    openai_api_key = os.getenv("openai_api_key")
    llm = ChatOpenAI(api_key=openai_api_key, model=llm_model_name, temperature=0)

    return llm

## 3. Agents Overview

### 3.1 News Agent

<b>Focuses on market-moving catalysts.</b>

- Integrates web search (via DuckDuckGo or custom search_news_tool) to retrieve current headlines.

- Summarizes sentiment and relevance using an LLM prompt template.

- Outputs structured findings that downstream agents can interpret.

<b>Tools used:</b>

- duckduckgo_search for headline discovery

- langchain.tools for tool registration

- ChatPromptTemplate for templated prompts

#### News Agent Tools

In [ ]:
from langchain.tools import tool
try:
    from duckduckgo_search import DDGS
except Exception:
    DDGS = None

@tool("search_news", return_direct=False)
def search_news_tool(query: str, max_results: int = 5) -> str:
    """
    Search latest headlines & snippets relevant to a stock or topic.
    Uses duckduckgo_search as a simple public news proxy.
    Returns a concise, newline-separated list of 'title — url'.
    """
    if DDGS is None:
        return ("duckduckgo_search not installed. "
                "Install with `pip install duckduckgo-search` "
                "or replace this tool with your news API.")
    items = []
    with DDGS() as ddgs:
        for r in ddgs.news(query, timelimit="7d", max_results=max_results):
            title = r.get("title", "")[:160]
            url = r.get("url", "")
            if title and url:
                items.append(f"{title} — {url}")
    if not items:
        return "No recent news found."
    return "\n".join(items)

#### News Agent

In [ ]:
from langchain.agents import AgentExecutor, create_tool_calling_agent
from langchain.prompts import ChatPromptTemplate, MessagesPlaceholder
from agents.news_agent.tools import search_news_tool

news_agent_system = (
  "You are a News Analyst. Use the search tool to gather 5-8 recent, credible items."
  "Synthesize themes, risks, catalysts, and sentiment for investors. Output a concise"
  "markdown summary with bullet points and 1-2 short citations (URLs)."
)

def create_news_agent(model) -> AgentExecutor:

    prompt = ChatPromptTemplate.from_messages(
        [
            ("system", news_agent_system),
            ("human", "{input}"),
            MessagesPlaceholder("agent_scratchpad"),
        ]
    )
    agent = create_tool_calling_agent(llm=model, tools=[search_news_tool], prompt=prompt)

    return AgentExecutor(agent=agent, tools=[search_news_tool], verbose=False, handle_parsing_errors=True)

### 3.2 Earnings Agent

<b>Analyzes corporate earnings reports and financial statements.</b>

- Parses key performance indicators (revenue, EPS, margins).

- Compares against consensus estimates.

- Produces a concise summary and sentiment classification (positive/neutral/negative).

Uses similar modular design — each step encapsulated in a callable tool or agent chain.

#### Earnings Agent Tools

In [ ]:
from langchain.tools import tool
import yfinance as yf
import datetime as dt

@tool("fetch_earnings", return_direct=False)
def fetch_earnings_tool(ticker: str) -> str:
    """
    Fetch upcoming and recent earnings info via yfinance.
    Returns a concise summary (dates + surprises if available).
    """
    tk = yf.Ticker(ticker)
    lines = [f"EARNINGS SNAPSHOT for {ticker.upper()}"]

    # Upcoming earnings (earnings_dates includes future dates)
    try:
        ed = tk.earnings_dates  # DataFrame if available
        if ed is not None and not ed.empty:
            # Take the next upcoming date and last reported
            ed_sorted = ed.sort_index()
            upcoming = ed_sorted[ed_sorted.index >= dt.datetime.now().date()]
            last = ed_sorted[ed_sorted.index < dt.datetime.now().date()]
            if not upcoming.empty:
                lines.append(f"Upcoming: {upcoming.index[0].strftime('%Y-%m-%d')}")
            if not last.empty:
                # Try EPS surprise columns if present
                row = last.iloc[-1]
                surprise = None
                for k in ["EPS Surprise %", "Surprise(%)", "epssurprisepct", "epssurprisepercent"]:
                    if k in row and row[k] is not None:
                        surprise = row[k]
                        break
                lines.append(
                    f"Last reported: {last.index[-1].strftime('%Y-%m-%d')}"
                    + (f", EPS surprise: {surprise}" if surprise is not None else "")
                )
        else:
            lines.append("No earnings_dates available.")
    except Exception as e:
        lines.append(f"earnings_dates unavailable: {e}")

    # Quarterly financials (very high-level)
    try:
        qf = tk.quarterly_financials
        if qf is not None and not qf.empty:
            cols = list(qf.columns)
            if cols:
                last_q = cols[0]
                revenue = qf.loc["Total Revenue", last_q] if "Total Revenue" in qf.index else None
                gross_profit = qf.loc["Gross Profit", last_q] if "Gross Profit" in qf.index else None
                lines.append(f"Last quarter ({last_q.date()}): Revenue={revenue}, GrossProfit={gross_profit}")
    except Exception:
        pass

    return "\n".join(lines)

#### Earnings Agent

In [ ]:
from langchain.agents import AgentExecutor, create_tool_calling_agent
from langchain.prompts import ChatPromptTemplate, MessagesPlaceholder
from agents.earnings_agent.tools import fetch_earnings_tool

earnings_agent_system = (
  "You are an Earnings Analyst. Use the earnings tool to summarize the latest and upcoming"
  "earnings information (dates, surprises if available) and key line items. Provide a "
  "short view on momentum and watchouts. Output concise markdown."
)

def create_earnings_agent(model) -> AgentExecutor:

    prompt = ChatPromptTemplate.from_messages(
        [
            ("system", earnings_agent_system),
            ("human", "{input}"),
            MessagesPlaceholder("agent_scratchpad"),
        ]
    )
    agent = create_tool_calling_agent(llm=model, tools=[fetch_earnings_tool], prompt=prompt)

    return AgentExecutor(agent=agent, tools=[fetch_earnings_tool], verbose=False, handle_parsing_errors=True)

### 3.3 Market Agent

Integrates quantitative signals (stock trends, volatility, RSI, etc.) with textual insights from the other agents.
Performs reasoning over structured market data and qualitative narratives to identify actionable opportunities.

#### Market Agent Tools

In [ ]:
from langchain.tools import tool
import yfinance as yf
import datetime as dt

@tool("fetch_market_snapshot", return_direct=False)
def fetch_market_snapshot_tool(ticker: str) -> str:
    """
    Pulls basic market snapshot with yfinance: price, change, volume, valuation.
    Returns a compact textual snapshot.
    """
    tk = yf.Ticker(ticker)
    info = {}
    try:
        price = tk.fast_info.last_price
        prev_close = tk.fast_info.previous_close
        change = None
        if price is not None and prev_close:
            change = (price - prev_close) / prev_close * 100
        info.update({
            "price": price, "prev_close": prev_close, "pct_change": change,
            "market_cap": tk.fast_info.market_cap, "volume": tk.fast_info.last_volume,
            "currency": tk.fast_info.currency
        })
    except Exception as e:
        return f"Market snapshot failed: {e}"

    lines = [f"MARKET SNAPSHOT for {ticker.upper()}"]
    lines.append(f"Price: {info.get('price')} {info.get('currency')}")
    if info.get("pct_change") is not None:
        lines.append(f"Day change: {info['pct_change']:.2f}%")
    lines.append(f"Market Cap: {info.get('market_cap')}")
    lines.append(f"Volume: {info.get('volume')}")
    return "\n".join(lines)

#### Market Agent

In [ ]:
from langchain.agents import AgentExecutor, create_tool_calling_agent
from langchain.prompts import ChatPromptTemplate, MessagesPlaceholder
from agents.market_agent.tools import fetch_market_snapshot_tool
from pathlib import Path
import yaml

market_agent_system = (
  "You are a Market & Valuation Analyst. Use the market snapshot tool to extract current" 
  "trading context and discuss short-term technicals/flow and high-level valuation notes." 
  "Output concise markdown."
)


def create_market_agent(model) -> AgentExecutor:

    prompt = ChatPromptTemplate.from_messages(
        [
            ("system", market_agent_system),
            ("human", "{input}"),
            MessagesPlaceholder("agent_scratchpad"),
        ]
    )
    agent = create_tool_calling_agent(llm=model, tools=[fetch_market_snapshot_tool], prompt=prompt)

    return AgentExecutor(agent=agent, tools=[fetch_market_snapshot_tool], verbose=False, handle_parsing_errors=True)

## 4. Workflow

This section defines the coordination logic and workflow orchestration:

- Supervisor Agent routes queries to relevant specialists (news, earnings, or market).

- Tool execution is dynamically selected based on the input context.

- Memory and reflection allow the system to carry forward past reasoning chains.

- Prompts are defined using ChatPromptTemplate, and YAML configuration supports modular editing.

### 4.1 Graph Nodes

In [ ]:
from langchain.agents import AgentExecutor
from workflow.graph_state import GraphState

news_user_prompt = "Research recent news for {ticker}. Focus on price-moving catalysts."
earnings_user_prompt = "Analyze earnings for {ticker}. Summarize last and upcoming earnings. Use the tool."
market_user_prompt = "Provide a market snapshot for {ticker}. Use the tool."

AGENTS = ["news", "earnings", "market"]

def news_node(state: GraphState, agent: AgentExecutor) -> GraphState:
    ticker = state["ticker"]
    query = news_user_prompt.format(ticker=ticker)
    res = agent.invoke({"input": query})
    state["news_summary"] = res["output"]
    state["completed"] = list(set(state["completed"] + ["news"]))
    return state


def earnings_node(state: GraphState, agent: AgentExecutor) -> GraphState:
    ticker = state["ticker"]
    query = earnings_user_prompt.format(ticker=ticker)
    res = agent.invoke({"input": query})
    state["earnings_summary"] = res["output"]
    state["completed"] = list(set(state["completed"] + ["earnings"]))
    return state


def market_node(state: GraphState, agent: AgentExecutor) -> GraphState:
    ticker = state["ticker"]
    query = market_user_prompt.format(ticker=ticker)
    res = agent.invoke({"input": query})
    state["market_summary"] = res["output"]
    state["completed"] = list(set(state["completed"] + ["market"]))
    return state


def synth_node(state: GraphState, synthesizer_chain) -> GraphState:
    out = synthesizer_chain.invoke(
        {
            "ticker": state["ticker"],
            "news_summary": state.get("news_summary", ""),
            "earnings_summary": state.get("earnings_summary", ""),
            "market_summary": state.get("market_summary", ""),
        }
    )
    state["final_recommendation"] = out.content if hasattr(out, "content") else str(out)
    return state
    
def supervisor_node(state: GraphState) -> GraphState:
    # Do any bookkeeping here if needed; otherwise just pass state through
    return state

def supervisor_router(state: GraphState) -> str:
    remaining = [a for a in AGENTS if a not in state.get("completed", [])]
    return remaining[0] if remaining else "synth"

### 4.2 Graph State

In [ ]:
from typing import TypedDict, List, Optional, Dict, Any

class GraphState(TypedDict):
    ticker: str
    query: str  # general query / task
    # outputs collected from agents
    news_summary: Optional[str]
    earnings_summary: Optional[str]
    market_summary: Optional[str]
    # bookkeeping
    completed: List[str]
    # final
    final_recommendation: Optional[str]

### 4.3 Agents Workflow

In [ ]:
from langchain.prompts import ChatPromptTemplate, MessagesPlaceholder
import yaml
from langgraph.graph import StateGraph, END

from agents.earnings_agent.earnings_agent import create_earnings_agent
from agents.market_agent.market_agent import create_market_agent
from agents.news_agent.news_agent import create_news_agent
from model.init_model import init_main_model
from workflow.graph_state import GraphState
from workflow.nodes.nodes import news_node, earnings_node, market_node, synth_node, supervisor_node, AGENTS, supervisor_router
from pathlib import Path

system_synthesizer = (
  "You are the Lead Portfolio Analyst. Merge inputs from News, Earnings, and Market agents." 
  "Produce a final, actionable recommendation block (Buy/Hold/Sell with confidence 0-1)," 
  "key drivers (bull/bear), near-term catalysts, and 2-3 risks. Be concise and concrete."
)

human_synthesizer = (
  "Ticker: {ticker}\n\n"
  "### News Summary\n{news_summary}\n\n"
  "### Earnings Summary\n{earnings_summary}\n\n"
  "### Market Summary\n{market_summary}\n\n"
  "Write the final recommendation now."
)

def make_synthesizer(model):
    """Final writer to merge all agent outputs into actionable recommendations."""
    template = ChatPromptTemplate.from_messages(
        [
            ("system", system_synthesizer),
            ("human", human_synthesizer)
        ]
    )
    return template | model  # LC chain: Prompt -> LLM

def build_agents_workflow(llm_model_name):
    # --- Base LLM for agents & synthesizer, we can initiate different models for agents here ---
    model = init_main_model(llm_model_name)

    # --- Create specialized agents ---
    news_agent = create_news_agent(model)
    earnings_agent = create_earnings_agent(model)
    market_agent = create_market_agent(model)

    # --- Create synthesizer chain ---
    synthesizer = make_synthesizer(model)

    # --- LangGraph: wire nodes ---
    g = StateGraph(GraphState)

    # Bind node callables with their dependencies via closures
    g.add_node("news", lambda s: news_node(s, news_agent))
    g.add_node("earnings", lambda s: earnings_node(s, earnings_agent))
    g.add_node("market", lambda s: market_node(s, market_agent))
    g.add_node("synth", lambda s: synth_node(s, synthesizer))

    # Supervisor node
    g.add_node("supervisor", supervisor_node)
    # Edges: start -> supervisor -> (news|earnings|market|synth) -> supervisor ... -> synth -> END
    g.set_entry_point("supervisor")

    for a in AGENTS:
        g.add_edge(a, "supervisor")
    g.add_edge("synth", END)

    # Route decisions come from the router function (returns a string)
    g.add_conditional_edges(
        "supervisor",
        supervisor_router,   # returns: "news" | "earnings" | "market" | "synth"
        {
            "news": "news",
            "earnings": "earnings",
            "market": "market",
            "synth": "synth",
        },
    )

    return g.compile()

## 5 Run

In [ ]:
from workflow.agents_workflow import build_agents_workflow
from workflow.graph_state import GraphState

# Run locally without gradio

app = build_agents_workflow(llm_model_name="gpt-4o-mini")

def run_user_query(ticker):
    QUERY = f" Produce investor-ready insights for {ticker}."
    init_state: GraphState = {
        "ticker": ticker,
        "query": QUERY,
        "news_summary": None,
        "earnings_summary": None,
        "market_summary": None,
        "completed": [],
        "final_recommendation": None,
    }
    final_state = app.invoke(init_state)

    return final_state

state = run_user_query("AAPL")

print("\n" + "=" * 80)
print(f"### NEWS SUMMARY\n{state['news_summary']}\n")
print(f"### EARNINGS SUMMARY\n{state['earnings_summary']}\n")
print(f"### MARKET SUMMARY\n{state['market_summary']}\n")
print(f"### FINAL RECOMMENDATION\n{state['final_recommendation']}\n")

## 6. System Architecture Summary

| **Component**        | **Description**                                 |
| -------------------- | ----------------------------------------------- |
| **Supervisor Agent** | Plans, routes, and consolidates results         |
| **News Agent**       | Gathers market news and sentiment               |
| **Earnings Agent**   | Extracts and interprets company earnings data   |
| **Market Agent**     | Analyzes stock trends and technical indicators  |
| **Evaluator Agent**  | Critiques and scores the overall report         |
| **Memory Layer**     | Maintains conversational and analytical context |
| **Iteration Loop**   | Refines reasoning via feedback cycles           |

<b>Key Strengths</b>
✅ Modular YAML + LangChain integration for reusable prompt templates.
✅ Realistic workflow emulating professional equity research teams.
✅ Self-evaluating loop ensures higher factual consistency.
✅ Extensible for additional agents (e.g., ESG Analyst, Risk Scorer).


## 7. Conclusion

The Multi-Agent Financial Analysis System exemplifies next-generation AI infrastructure for market intelligence — one that reasons, collaborates, and evolves.
By blending structured reasoning with self-improvement loops, it brings the intelligence of multi-analyst teams into an automated, explainable framework for financial decision-making.

## 8. Appendix 